# Librerías


In [107]:
import pandas as pd
import numpy as np

from functools import reduce

import  plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt 
import cufflinks as cf 
import seaborn as sns



import os


from varclushi import VarClusHi
from sklearn.impute import SimpleImputer
from scipy import stats
from sklearn.feature_selection import VarianceThreshold
from sklearn.feature_selection import SelectKBest
from sklearn.metrics import mean_absolute_error, r2_score
from sklearn.preprocessing import StandardScaler



import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


pd.set_option('display.float_format', lambda x: '%.3f' % x)

pd.set_option('display.max_rows', 900)
cf.go_offline()

# Carga de Datos

In [2]:
path = r"C:\Users\mi18092\venv_test\DATA\Kaggle_StoreSalesComp".replace('\\','\\')

In [3]:
df = pd.read_csv(os.path.join(path, 'train.csv'))

stores = pd.read_csv(os.path.join(path, 'stores.csv'))

holidays = pd.read_csv(os.path.join(path, 'holidays_events.csv'))

transactions = pd.read_csv(os.path.join(path, 'transactions.csv'))

oil = pd.read_csv(os.path.join(path, 'oil.csv'))

# Pretatamiento/Limpieza de datos


In [4]:
df['date'] = pd.to_datetime(df['date'])

df = df.merge(stores, on='store_nbr')

In [5]:
df['month'] = df.date.map(lambda x : x.month)
df['weekday'] = df.date.map(lambda x : x.weekday())

df['day'] = df.date.map(lambda x : x.day)

## Holidays

In [6]:
holidays['date'] = pd.to_datetime(holidays['date'])

holidays = holidays.loc[holidays['transferred']==False]
holidays.drop(['transferred'],axis=1, inplace=True)

In [7]:
class_holiday  ={'Día Terremoto Manabi':['Terremoto Manabi'],
'Días Post Terrem 1-7':['Terremoto Manabi+1', 'Terremoto Manabi+2', 'Terremoto Manabi+3',
'Terremoto Manabi+4', 'Terremoto Manabi+5', 'Terremoto Manabi+6',
'Terremoto Manabi+7'], 
'Días Post Terrem 8-15':['Terremoto Manabi+8', 'Terremoto Manabi+9','Terremoto Manabi+10', 'Terremoto Manabi+11',
'Terremoto Manabi+12', 'Terremoto Manabi+13','Terremoto Manabi+14', 'Terremoto Manabi+15'],
'Días Post Terrem +15':['Terremoto Manabi+16', 'Terremoto Manabi+17',
'Terremoto Manabi+18', 'Terremoto Manabi+19','Terremoto Manabi+20', 'Terremoto Manabi+21',
'Terremoto Manabi+22', 'Terremoto Manabi+23','Terremoto Manabi+24', 'Terremoto Manabi+25',
'Terremoto Manabi+26', 'Terremoto Manabi+27','Terremoto Manabi+28', 'Terremoto Manabi+29','Terremoto Manabi+30'],
'Fundacion':['Fundacion de Manta','Fundacion de Cuenca','Fundacion de Machala',
'Fundacion de Santo Domingo','Fundacion de Esmeraldas','Fundacion de Riobamba',
'Fundacion de Ambato','Fundacion de Ibarra','Fundacion de Loja'],
'Fundacion de Quito': ['Fundacion de Quito-1','Fundacion de Quito','Traslado Fundacion de Quito'],
'Fundacion de Guayaquil':['Fundacion de Guayaquil-1','Fundacion de Guayaquil','Traslado Fundacion de Guayaquil'],
'Mundial de Futbol':['Inauguracion Mundial de futbol Brasil',
'Mundial de futbol Brasil: Ecuador-Suiza','Mundial de futbol Brasil: Ecuador-Honduras',
'Mundial de futbol Brasil: Ecuador-Francia','Mundial de futbol Brasil: Octavos de Final',
'Mundial de futbol Brasil: Cuartos de Final','Mundial de futbol Brasil: Semifinales',
'Mundial de futbol Brasil: Tercer y cuarto lugar','Mundial de futbol Brasil: Final'],
'Cantonizacion':['Cantonizacion de Libertad','Cantonizacion de Riobamba',
'Cantonizacion del Puyo','Cantonizacion de Guaranda',
'Cantonizacion de Latacunga','Cantonizacion de El Carmen',
'Cantonizacion de Cayambe','Cantonizacion de Quevedo',
'Cantonizacion de Salinas'],
'Independencia':['Primer Grito de Independencia',
'Traslado Primer Grito de Independencia'],
'Independencia Local': ['Traslado Independencia de Guayaquil',
'Independencia de Cuenca','Independencia de Guaranda',
'Independencia de Latacunga','Independencia de Ambato',
'Independencia de Guayaquil'],
'Temporada Navideña':['Navidad-4',
'Navidad-3','Navidad-2','Puente Navidad',
'Navidad-1','Navidad','Navidad+1','Recupero puente Navidad',
'Recupero Puente Navidad'],
'Día de la Madre':['Dia de la Madre-1', 'Dia de la Madre'],
'1 enero': ['Puente Primer dia del ano',
'Primer dia del ano-1', 'Primer dia del ano',
'Traslado Primer dia del ano','Recupero puente primer dia del ano','Recupero Puente Primer dia del ano'],
'Carnaval':['Carnaval'],
'Provincialización':['Provincializacion de Cotopaxi','Provincializacion de Imbabura',
'Provincializacion de Santo Domingo','Provincializacion Santa Elena'],
'Difuntos':['Puente Dia de Difuntos','Recupero Puente Dia de Difuntos','Dia de Difuntos'],
'Batalla de Piuchincha':['Traslado Batalla de Pichincha','Batalla de Pichincha'],
'Viernes Santo':['Viernes Santo'], 
'Dia del Trabajo':['Dia del Trabajo'],
'Black Friday':['Black Friday'],
'Cyber Monday':['Cyber Monday']
}


In [8]:
holidays['id_date'] = holidays['date'].map(lambda x :str(x.year)+str(x.month).zfill(2)+str(x.day).zfill(2)).astype(int)

df['id_date'] = df['date'].map(lambda x :str(x.year)+str(x.month).zfill(2)+str(x.day).zfill(2)).astype(int)

In [9]:
mapeo_class = {}
for i in holidays.description.unique():
    for key, value in class_holiday.items():
        if i in value:
            mapeo_class[i] = key

In [10]:
holidays['class'] = holidays.description.replace(mapeo_class)

## Oil and transactions

In [11]:
oil['date'] = pd.to_datetime(oil['date'])
transactions['date'] = pd.to_datetime(transactions['date'])

In [12]:
oil['id_date'] = oil['date'].map(lambda x :str(x.year)+str(x.month).zfill(2)+str(x.day).zfill(2)).astype(int)

transactions['id_date'] = transactions['date'].map(lambda x :str(x.year)+str(x.month).zfill(2)+str(x.day).zfill(2)).astype(int)

In [13]:
df = df.merge(oil.set_index('id_date')[['dcoilwtico']], on='id_date', how='left')

df = df.merge(transactions[['id_date', 'store_nbr','transactions']], on=['id_date','store_nbr'], how='left')

# Variable objetivo

In [14]:
um = ['id_date', 'store_nbr']

In [15]:
y = df.groupby(um).agg({'sales':'sum'}).reset_index()
y.sample(4)

id_date  store_nbr     sales
8563   20130608         32  3183.184
30915  20140728         28  8885.971
39056  20141227         15  6894.180
31019  20140730         24 18672.724

In [16]:
y.sales.describe(percentiles=np.linspace(.01,.99,10)).to_frame().T

count      mean      std   min    1%    11.9%    22.8%    33.7%  \
sales 90936.000 11806.600 9925.500 0.000 0.000 3516.844 5338.076 6845.834   

         44.6%      50%     55.4%     66.3%     77.2%     88.1%       99%  \
sales 8449.456 9323.822 10277.131 12558.483 15794.574 21684.914 49742.478   

             max  
sales 136457.427

Como podemos ver en el histograma de abajo, hay una relativamente grande cantidad de valores en cero, el resto se ven bien distribuidos. Dado que estos valores que están como cero pueden afectar nuestras estimaciones, debemos analizar si hay un patrón en ellos o si son valores reales que debamos tomar en cuenta.

In [17]:
px.histogram(y.sales, marginal='box')

Primero, podemos examinar la serie de tiempo de las ventas, la tendencia que estas han tenido y si los valores en cero hacen sentido con esta tendencia.

In [18]:
df.groupby(['date']).agg({'sales':'sum'}).iplot(xTitle='Fecha', yTitle='Ventas', color='blue', theme='white')

Podemos ver que hay ciertos ciclos en las ventas (muy probablemente de forma anual) pero que en general se cuenta con una tendencia positiva. Para ver esto con mayor claridad podemos graficar el Moving Average a 5 días por ejemplo:

In [19]:
plot_moving_average = lambda dias : df.groupby(['date']).agg({
    'sales':'sum'}).rolling(dias).mean().iplot(yTitle='sales', xTitle='fecha', color='blue')

In [20]:
plot_moving_average(5)

In [21]:
df.groupby(['date']).agg({'sales':'sum'}).rolling(10).mean().to_csv('sales_ma10.csv')

En la gráfica anterior podemos ver la tendencia de forma más clara..

Finalmente, podemos analizar el comportamineto de los valores que son zero, los cuales deberían de tener una tendencia a la baja a través del tiempo.

In [22]:
y['zeros']  = (y['sales'] == 0).astype(int)

y['month'] = y['id_date'].map(lambda x : str(x)[:6])

y.groupby(['month']).agg({'zeros':'sum'}).iplot(yTitle='Cantidad de Ventas en 0 en el mes', xTitle='Mes (yyyyMM)')

In [23]:
y.drop(['month', 'zeros'], axis=1, inplace=True)

Viendo la gráfica anterior, podemos confirmar que hay una disminución en los valores cero, por lo que podemos concluir que los valores cero no son atípicos,.

# Ingeniería de Datos

## Ventanas Móviles

In [24]:
windows = df.id_date.drop_duplicates().reset_index(drop=True).reset_index().rename(columns={'index':'id_wind'})

In [25]:
obs_w_1, obs_w_2  = 3, 7

i_w, f_w = windows.id_wind.min(),  int(np.round(windows.id_wind.max()*.8))
obs_w_1, obs_w_2  = 3, 7
pred_w = 1

i_anc1, f_anc = i_w+obs_w_1, f_w-pred_w
anchors1 = range(i_anc1, f_anc +1)

i_anc2 = i_w+obs_w_2
anchors2 = range(i_anc2, f_anc +1)

In [26]:
i_test_anc, f_test_anc = f_w+1, windows.id_wind.max()-pred_w

In [27]:
df = df.merge(windows, on='id_date', how='left')

y = y.merge(windows, on='id_date', how='left')

## Variables Ventas Totales

In [28]:
def overall_past_sales(ancla:int, days:int):
    aux = df.loc[(df['id_wind']>ancla-days-1) & (df['id_wind']<ancla) ][['sales']+um]
    return pd.DataFrame({'ancla':[ancla], f'x_overall_sales_{days}':[aux.sales.sum()]})

cruzar = lambda x,y:pd.merge(x,y,on='ancla',how='outer')

In [29]:
Xt = reduce(cruzar,map(lambda k: pd.concat(map(lambda anc : overall_past_sales(anc,k), 
                                   range(i_w+k,f_anc+1)), ignore_index=True),[obs_w_1,obs_w_2]))

Xv = reduce(cruzar,map(lambda k: pd.concat(map(lambda anc : overall_past_sales(anc,k), 
                                   range(i_test_anc+k,f_test_anc+1)), ignore_index=True),[obs_w_1,obs_w_2]))

## Variables Ventas por Ciudad, Estado, Cluster, Tipo de Tienda

In [30]:
def group_past_sales(ancla:int, days:int, group:str, l:list=None):

    aux = df.loc[(df['id_wind']>ancla-days-1) & (df['id_wind']<ancla) ]
    if l is None:
        aux =  aux.groupby([group]).agg({'sales':'sum'}).reset_index()
    else : 
        aux =  aux.groupby([group]+l).agg({'sales':'sum'}).reset_index()
    aux.rename(columns={'sales':f'x_{group}_sales_{days}'}, inplace=True)        
    aux.insert(0, 'ancla', ancla)
    return aux

In [31]:
gen_var = lambda col, i_w, f_w: reduce(lambda x,y:pd.merge(x,y,on=['ancla',col],how='outer'),
                             map(lambda k: pd.concat(map(lambda anc : group_past_sales(anc,k, col), 
                                                         range(i_w+k,f_w+1)), ignore_index=True),[obs_w_1,obs_w_2]))

In [32]:
variables_t = {col : gen_var(col, i_w, f_anc+1) for col in ['city','state', 'type', 'cluster']}

In [33]:
variables_v = {col : gen_var(col, i_test_anc, f_test_anc+1) for col in ['city','state', 'type', 'cluster']}

## Ventas pasadas por tienda (individual)

In [34]:
stores_sales_t = reduce(lambda x,y:pd.merge(x,y,on=['ancla','store_nbr','city','state','cluster','type'],how='outer'),
                             map(lambda k: pd.concat(map(lambda anc : group_past_sales(anc,k, 'store_nbr',['state','city','cluster','type']), 
                                                         range(i_w+k,f_w+1)), ignore_index=True),[obs_w_1,obs_w_2]))

In [35]:
stores_sales_v = reduce(lambda x,y:pd.merge(x,y,on=['ancla','store_nbr','city','state','cluster','type'],how='outer'),
                             map(lambda k: pd.concat(map(lambda anc : group_past_sales(anc,k, 'store_nbr',['state','city','cluster','type']), 
                                                         range(i_test_anc+k,f_test_anc+1)), ignore_index=True),[obs_w_1,obs_w_2]))

In [36]:
Xt = stores_sales_t.merge(Xt, on='ancla')

Xv = stores_sales_v.merge(Xv, on=['ancla'])

In [37]:
for k, v in variables_t.items():
    Xt = Xt.merge(v, on=['ancla',k], how='inner')
    
    
for k, v in variables_v.items():
    Xv = Xv.merge(v, on=['ancla',k], how='inner')

In [38]:
def suma_inc(l):
    return sum( [int( y>x ) for x,y in zip( l, l[1:] )] )

def per_inc(l):
    return np.mean( [int( y>x ) for x,y in zip( l, l[1:] )] )

def med_inc(l):
    return np.mean( [(y-x)  for x,y in zip( l, l[1:] )] )

def media_dec(l):
    return np.mean( [int( y<x ) for x,y in zip( l, l[1:] )] )

def delta_min(l):
    try:
        return min( [float( y-x ) for x,y in zip( l, l[1:] ) ] )
    except:
        return np.nan
    
def delta_max(l):
    try:
        return max( [float( y-x ) for x,y in zip( l, l[1:] ) ] )
    except:
        return np.nan
    
def delta_media(l):
    try:
        return np.mean( [float( y-x ) for x,y in zip( l, l[1:] ) ] )
    except:
        return np.nan

def delta_desv(l):
    try:
        return np.std( [float( y-x ) for x,y in zip( l, l[1:] ) ] )
    except:
        return np.nan

def pct_delta_media(l):
    try:
        return np.mean([ float(y-x)/x  for x,y in zip( l , l[1:] ) ]  )
    except:
        return np.nan

def max_racha_inc(l):
    return max([len(i) for i in  "".join([ str(int(y>x)) for x,y in zip(l , l[1:]) ]).split('0')])

def max_racha_dec(l):
    return max([len(i) for i in  "".join([ str(int(y>x)) for x,y in zip(l , l[1:]) ]).split('1')])

def media_racha_inc(l):
    return np.mean([len(i) for i in  "".join([ str(int(y>x)) for x,y in zip(l , l[1:]) ]).split('0')])

def media_racha_dec(l):
    return np.mean([len(i) for i in  "".join([ str(int(y>x)) for x,y in zip(l , l[1:]) ]).split('1')])

In [39]:
lst_func = ['std','min','mean','max', suma_inc, 
med_inc,media_dec, delta_min,delta_max,
delta_media,delta_desv,pct_delta_media,
max_racha_inc,max_racha_dec,media_racha_inc,media_racha_dec]

In [40]:
def variable_explosion(ancla:int, days:int):
    aux = df.loc[(df['id_wind']>ancla-days-1) & (df['id_wind']<ancla) ]

    aux = aux.groupby(['id_wind','store_nbr']).agg({'sales':'sum'}).reset_index()

    aux = aux.pivot_table(index=['store_nbr'],  values = 'sales', aggfunc=lst_func)

    aux.columns = [f'x_{i[0]}_{i[1]}_{days}' for i in aux.columns]

    aux.reset_index(inplace=True) 
    aux.insert(0, 'ancla',ancla)
    return aux
    

In [41]:
cruzar = lambda x,y:pd.merge(x,y,on=['ancla','store_nbr'],how='outer')

X_t = reduce(cruzar,map(lambda k: pd.concat(map(lambda anc : variable_explosion(anc,k), 
                                   range(i_w+k,f_w)), ignore_index=True),[obs_w_1,obs_w_2]))

X_v = reduce(cruzar,map(lambda k: pd.concat(map(lambda anc : variable_explosion(anc,k), 
                                   range(i_test_anc+k,f_test_anc)), ignore_index=True),[obs_w_1,obs_w_2]))

In [42]:
Xt = Xt.merge(X_t, on=['ancla','store_nbr'])
Xv  = Xv.merge(X_v, on=['ancla','store_nbr'])

## Vaiables por Familia del Producto

In [43]:
def variables_family_prod(ancla:int, days:int):
    aux = df.loc[(df['id_wind']>ancla-days-1) & (df['id_wind']<ancla) ]
    aux = aux.pivot_table(index='store_nbr', columns='family', values='sales', aggfunc=[np.mean, np.sum, np.std])#.reset_index()

    aux.columns = [f'x_{c}_{d}_{days}' for c,d in aux.columns]

    aux.reset_index(inplace=True)

    aux.insert(0, 'ancla', ancla)
    return aux 

In [44]:
var_fam_xt = reduce(lambda x , y : x.merge(y, on=['ancla','store_nbr'], how='outer')
                    ,map(lambda k : pd.concat(map(lambda x: variables_family_prod(x,k),
                                                  range(i_w+k,f_anc+1))), [obs_w_1, obs_w_2]))

In [45]:
var_fam_xv = reduce(lambda x , y : x.merge(y, on=['ancla','store_nbr'], how='outer')
                    ,map(lambda k : pd.concat(map(lambda x: variables_family_prod(x,k),
                                                  range(i_test_anc+k,f_test_anc+1))), [obs_w_1, obs_w_2]))

In [46]:
Xt = Xt.merge(var_fam_xt, on=['ancla','store_nbr'], how='outer')
Xv = Xv.merge(var_fam_xv, on=['ancla','store_nbr'], how='outer')

## Variables sobre las Promociones disponibles 

In [47]:
def onprom_transac(ancla:int, days:int):
    aux = df[(df['id_wind']<ancla) & (df['id_wind']>ancla-days-1)]

    aux = aux.groupby(['store_nbr']).agg({'transactions':[np.mean, np.median, np.max, np.std, suma_inc],                                        
                                               'onpromotion': [np.mean, np.max]})

    aux.columns =[f'x_{x}_{v}_{days}' for x, v in aux.columns]

    aux.reset_index(inplace=True)
    aux.insert(0, 'ancla', ancla)
    return aux

In [48]:
on_prom_xt = reduce(lambda x, y : x.merge(y, on=['ancla', 'store_nbr'], how='outer'),
                   map(lambda days : pd.concat(map(lambda an : onprom_transac(an, days), 
                            range(i_w+days, f_anc+1)), ignore_index=True), [obs_w_1, obs_w_2]))

In [49]:
on_prom_xv = reduce(lambda x, y : x.merge(y, on=['ancla', 'store_nbr'], how='outer'),
                   map(lambda days : pd.concat(map(lambda an : onprom_transac(an, days), 
                            range(i_test_anc+days, f_test_anc+1)), ignore_index=True), [obs_w_1, obs_w_2]))

In [50]:
Xt = Xt.merge(on_prom_xt, on=['ancla','store_nbr'], how='outer')
Xv = Xv.merge(on_prom_xv, on=['ancla','store_nbr'], how='outer')

## Variables por precios del Petróleo

In [51]:
oil = windows.merge(oil, on='id_date', how='left')

oil['date'] = pd.to_datetime(oil.id_date.map(lambda x : str(x)[:4]+'-'+str(x)[4:6]+'-'+str(x)[6:]))

oil['day'] = oil['date'].map(lambda x : x.day_name())

#oil[oil['dcoilwtico'].notnull()]['day'].value_counts()

Podemos ver que hay valores nulos en los precios del petroleo de  muchas fechas:

In [52]:
display(oil.isna().sum().to_frame().T)

display(oil[oil.dcoilwtico.isna()].day.value_counts().to_frame().iplot(kind='bar', yTitle='Días con Valores Nulos', xTitle='Día de la semana'))

id_wind  id_date  date  dcoilwtico  day
0        0        0     0         521    0

None

Como vemos, esto se debe a que no contamos con el precio en el fin de semana y en días festivos, por lo que para evitar tener nulos al crear nuestras variabeles se imputará con el valor del día anterior en el que no sea nulo.

In [53]:
oil[oil['dcoilwtico'].notnull()]['day'].value_counts()

oil['dcoilwtico'] = np.where(oil.day=='Saturday', oil.dcoilwtico.shift(1), oil.dcoilwtico)

oil['dcoilwtico']=np.where(oil.day=='Sunday', oil.dcoilwtico.shift(1), oil.dcoilwtico)

In [54]:
oil['dcoilwtico'] = np.where(oil.dcoilwtico.isna(), oil.dcoilwtico.shift(1), oil.dcoilwtico)

In [55]:
oil.drop(['day'], inplace=True, axis=1)

In [56]:
def oil_wind(ancla, days):
    aux = oil[(oil.id_wind<ancla) & (oil.id_wind>ancla-days-1)].copy()

    aux = np.array([[f'x_oil_{func.__name__}_{days}',func(aux.dcoilwtico.values)] for func in [np.mean, np.median, np.std]+lst_func[4:]])

    aux = pd.DataFrame(aux[:,1].reshape(1,15), columns =aux[:,0])

    aux.insert(0, 'ancla', ancla)
    return aux

In [57]:
oil_var_t =  reduce(lambda x, y :x.merge(y, on=['ancla'], how='outer'), map(lambda days : pd.concat(map(lambda x : oil_wind(x, days), 
                                range(i_w+days,f_anc+1))),[obs_w_1, obs_w_2]))

In [58]:
oil_var_v =  reduce(lambda x, y :x.merge(y, on=['ancla'], how='outer'), map(lambda days : pd.concat(map(lambda x : oil_wind(x, days), 
                                range(i_test_anc+days, f_test_anc+1))),[obs_w_1, obs_w_2]))

In [59]:
Xt = Xt.merge(oil_var_t, on='ancla', how='inner')

Xv = Xv.merge(oil_var_v, on='ancla', how='inner')

In [60]:
Xv = Xv.loc[Xv['ancla'] < 1682]

In [61]:
Xt.drop(['state','city','cluster','type'], inplace=True, axis=1)
Xv.drop(['state','city','cluster','type'], inplace=True, axis=1)
Xt.shape, Xv.shape

((72522, 288), (17928, 288))

In [62]:
for col in Xt.select_dtypes(['object']).columns:
    Xt[col] = pd.to_numeric(Xt[col], errors='coerce')
    Xv[col] = pd.to_numeric(Xv[col], errors='coerce')

In [63]:
var = [c for c in Xt.filter(like='x_').columns]

## Variables sobre Holidays

In [64]:
holidays = holidays.merge(windows, on='id_date')

In [65]:
for cl_hol in holidays['class'].unique():
    Xt[f'x_class_ev_{cl_hol}'] = Xt.ancla.isin(holidays.loc[holidays['class']==cl_hol].id_wind.to_list()).astype(int)
    Xv[f'x_class_ev_{cl_hol}'] = Xv.ancla.isin(holidays.loc[holidays['class']==cl_hol].id_wind.to_list()).astype(int)

for cl_hol in holidays.locale_name.unique():
    Xt[f'x_ev_locale_{cl_hol}'] = Xt.ancla.isin(holidays.loc[holidays['class']==cl_hol].id_wind.to_list()).astype(int)
    Xv[f'x_ev_locale_{cl_hol}'] = Xv.ancla.isin(holidays.loc[holidays['class']==cl_hol].id_wind.to_list()).astype(int)

## Variables por día de la semana y mes

In [66]:
windows['date'] = pd.to_datetime(windows.id_date.map(lambda x : str(x)[:4]+'-'+str(x)[4:6]+'-'+str(x)[6:]))

windows['x_mes'] = windows.date.dt.month
windows['x_day'] = windows.date.dt.day_of_week

In [67]:
Xt = Xt.merge(windows[['id_wind','x_mes','x_day']].rename(columns={'id_wind':'ancla'}), on='ancla', how='left')
Xv = Xv.merge(windows[['id_wind','x_mes','x_day']].rename(columns={'id_wind':'ancla'}), on='ancla', how='left')

# Análisis Exploratorio

In [68]:
var = [v for v in Xt.filter(like='x_')]

## Datos Ausentes

In [72]:
missings = Xt.isna().sum().to_frame().rename(columns={0:'% de Nulos'})/(len(Xt))
missings.sort_values(by='% de Nulos', ascending=False)[:10].iplot(kind='bar',yTitle='Varaibale', xTitle='% de Nulos')

In [73]:
Xt.drop(['x_pct_delta_media_sales_7'], axis=1, inplace=True)
Xv.drop(['x_pct_delta_media_sales_7'], axis=1, inplace=True)

In [74]:
var.remove('x_pct_delta_media_sales_7')

Dado que tenemos muchas variables con un porcentaje significativo de valores nulos vamos a imputarlos con la mediana, y ver si la distribución de la variable se vió afectada mediante una prueba de Kolmogorov-Smirnov, en donde comparamos la distribución imputada con la distribución original sin valores nulos.

In [75]:
si = SimpleImputer(strategy='median')
si.fit(Xt)

Xti = si.transform(Xt)

Xvi = si.transform(Xv)

Xti = pd.DataFrame(Xti, columns=Xt.columns)

Xvi = pd.DataFrame(Xvi, columns=Xv.columns)


In [76]:
ks = pd.DataFrame(zip(var,map(lambda v : stats.ks_2samp(Xti[v], Xt[v].dropna()).statistic, 
                              var)), columns=['v','ks']).sort_values(by='ks', ascending=False)
ks.set_index('v')[:10].iplot(kind='bar', xTitle='variable', yTitle='ks')

Dado que en ninguna variable se tiene un ks mayor a .05, vamos a retener todas.

In [77]:
Xt = Xti.copy()
Xv = Xvi.copy()

## Varianza Nula en las variables

Después vamos a ver si hay variables que tengan una nula varianza que puede que no termine siendo útil posteriormente.

In [82]:
vt = VarianceThreshold()
vt.fit(Xt[var])

VarianceThreshold()

In [79]:
var_fuera = [v for v, flag in zip(var,vt.get_support()) if not  flag]

In [80]:
print(f'Se excluyeron {len(var_fuera)} variables que tienen varianza nula')

Se excluyeron 30 variables que tienen varianza nula


In [81]:
Xt.drop(var_fuera, inplace=True, axis=1)
Xv.drop(var_fuera, inplace=True, axis=1)

var = [v for v in var if v not in var_fuera]

## Multicolinealidad

In [83]:
vc = VarClusHi(df=Xt,feat_list=var).varclus().rsquare.sort_values(by=['Cluster','RS_Ratio']).reset_index(drop=True)
#display(vc)
best = sorted(vc.groupby('Cluster').first()['Variable'])

In [84]:
display(vc)[:20]

Cluster                             Variable  RS_Own  RS_NC  RS_Ratio
0          0                     x_sum_CLEANING_7   0.922  0.708     0.268
1          0                    x_mean_CLEANING_7   0.922  0.708     0.268
2          0               x_mean_PERSONAL CARE_7   0.915  0.684     0.268
3          0                x_sum_PERSONAL CARE_7   0.915  0.684     0.268
4          0                    x_mean_CLEANING_3   0.912  0.692     0.286
5          0                     x_sum_CLEANING_3   0.912  0.692     0.286
6          0                         x_sum_DELI_7   0.887  0.626     0.303
7          0                        x_mean_DELI_7   0.887  0.626     0.303
8          0                x_sum_PERSONAL CARE_3   0.878  0.610     0.313
9          0               x_mean_PERSONAL CARE_3   0.878  0.610     0.313
10         0                        x_mean_DELI_3   0.875  0.612     0.324
11         0                         x_sum_DELI_3   0.875  0.612     0.324
12         0                   x_mean_GROCERY I_7   0.907  0.795     0.451
13         0                    x_sum_GROCERY I_7   0.907  0.795     0.451
14         0                    x_sum_GROCERY I_3   0.890  0.770     0.478
15         0                   x_mean_GROCERY I_3   0.890  0.770     0.478
16         0                     x_std_CLEANING_7   0.707  0.623     0.779
17         0                         x_std_DELI_7   0.739  0.677     0.807
18         0                x_std_PERSONAL CARE_7   0.635  0.565     0.839
19         0                  x_media_dec_sales_7   0.074  0.077     1.003
20         1                     x_mean_PRODUCE_3   0.917  0.674     0.256
21         1                      x_sum_PRODUCE_3   0.917  0.674     0.256
22         1                      x_sum_PRODUCE_7   0.914  0.669     0.260
23         1                     x_mean_PRODUCE_7   0.914  0.669     0.260
24         1                x_mean_PET SUPPLIES_7   0.899  0.624     0.270
25         1                 x_sum_PET SUPPLIES_7   0.899  0.624     0.270
26         1                x_mean_PET SUPPLIES_3   0.877  0.612     0.316
27         1                 x_sum_PET SUPPLIES_3   0.877  0.612     0.316
28         1      x_sum_PLAYERS AND ELECTRONICS_7   0.882  0.647     0.336
29         1     x_mean_PLAYERS AND ELECTRONICS_7   0.882  0.647     0.336
30         1                 x_std_PET SUPPLIES_7   0.843  0.566     0.361
31         1      x_sum_PLAYERS AND ELECTRONICS_3   0.855  0.643     0.405
32         1     x_mean_PLAYERS AND ELECTRONICS_3   0.855  0.643     0.405
33         1                      x_std_PRODUCE_7   0.800  0.576     0.470
34         1                      x_std_PRODUCE_3   0.741  0.504     0.523
35         1                 x_std_PET SUPPLIES_3   0.700  0.479     0.577
36         1      x_std_PLAYERS AND ELECTRONICS_7   0.735  0.612     0.684
37         1      x_std_PLAYERS AND ELECTRONICS_3   0.617  0.524     0.805
38         1                 x_onpromotion_amax_7   0.528  0.648     1.339
39         2                     x_oil_suma_inc_3   0.990  0.340     0.015
40         2                x_oil_max_racha_inc_3   0.990  0.340     0.015
41         2                x_oil_max_racha_dec_3   0.990  0.340     0.015
42         2              x_oil_media_racha_dec_3   0.922  0.271     0.108
43         2              x_oil_media_racha_inc_3   0.852  0.357     0.229
44         2                    x_oil_delta_max_3   0.569  0.424     0.748
45         3                   x_suma_inc_sales_3   0.986  0.334     0.022
46         3              x_max_racha_inc_sales_3   0.986  0.334     0.022
47         3              x_max_racha_dec_sales_3   0.986  0.334     0.022
48         3            x_media_racha_inc_sales_3   0.885  0.337     0.173
49         3            x_media_racha_dec_sales_3   0.863  0.320     0.201
50         3            x_transactions_suma_inc_3   0.540  0.230     0.598
51         3                  x_media_dec_sales_3   0.494  0.281     0.704
52         3                  

TypeError: 'NoneType' object is not subscriptable

## k- best

In [87]:
from sklearn.feature_selection import f_regression

In [88]:
yt = Xt[['ancla','store_nbr']].merge(y.rename(columns={'id_wind':'ancla'}), on=['ancla','store_nbr'])

yv = Xv[['ancla','store_nbr']].merge(y.rename(columns={'id_wind':'ancla'}), on=['ancla','store_nbr'])

In [91]:
sk = SelectKBest(score_func=f_regression)
sk.fit(Xt[var],yt['sales'])

SelectKBest(score_func=<function f_regression at 0x00000215FFAE6050>)

In [92]:
aux = pd.DataFrame(zip(var,sk.scores_),columns=['var','score']).set_index('var').sort_values(by='score',ascending=False)
#aux.iplot(kind='bar',color='purple')[:10]
aux = aux[aux.index.isin(var)]

In [93]:
aux[:25].iplot(kind='bar', color='purple')

In [95]:
sk = SelectKBest(score_func=f_regression, k=180)
sk.fit(Xt[var],yt['sales'])

SelectKBest(k=180, score_func=<function f_regression at 0x00000215FFAE6050>)

In [96]:
best = sk.get_feature_names_out()

In [281]:
aux2 = Xt.merge(yt, on=['ancla', 'store_nbr'])

var = ['x_store_nbr_sales_7', 'x_class_ev_Temporada Navideña']

aux2 = aux2[['ancla','store_nbr','sales']+ var]


In [296]:
aux2[aux2['x_class_ev_Temporada Navideña']==1].iplot(x='x_store_nbr_sales_7', y='sales', kind='scatter',
                                                    mode='markers', size=5, yTitle='Sales',
                                                     xTitle='x_store_nbr_sales_7', color='purple')

#  Escalamiento de los datos

In [97]:
var = [x for x in Xt.filter(like='x_').columns]

In [98]:
ss  = StandardScaler()
ss.fit(Xt[var])

Xt_ss = pd.DataFrame(ss.transform(Xt[var]), columns = Xt[var].columns)

Xv_ss = pd.DataFrame(ss.transform(Xv[var]), columns = Xv[var].columns)

# Modelo

## Red Neuronal con Tensorflow Keras

In [100]:
import tensorflow as tf
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense

In [101]:
model = Sequential([
    Dense(units=70, activation='relu'),
    Dense(units=20, activation='selu'),
    Dense(units=20, activation='selu'),
    Dense(units=30, activation='relu'),
    Dense(units=1, activation='relu')
])

In [105]:
model.compile(loss=tf.keras.losses.MeanAbsoluteError(), 
             optimizer=tf.keras.optimizers.Adam())

model.fit(Xt_ss[best], yt['sales'], epochs=55, verbose=0)

In [103]:
def print_metrics(metric, yt_real, yv_real, yt, yv):
    print(f'The {metric.__name__} in the training set is :{metric(yt_real, yt)} ' )
    print(f'The {metric.__name__} in the validation set is :{metric(yv_real,yv)} ' )


In [334]:
yt_hat = model.predict(Xt_ss[best])
yv_hat = model.predict(Xv_ss[best])

print_metrics(mean_absolute_error, yt['sales'], yv['sales'], yt_hat, yv_hat)

print_metrics(r2_score, yt['sales'], yv['sales'], yt_hat, yv_hat)

561/561 [==============================] - 1s 1ms/step
The mean_absolute_error in the training set is :1281.2929861297534 
The mean_absolute_error in the validation set is :2296.9462992047856 
The r2_score in the training set is :0.9323841783860302 
The r2_score in the validation set is :0.8721987695537408 


In [109]:
yt['sales'].std(), yv['sales'].std()

(9271.158646434063, 11410.566453861067)

In [110]:
yt['sales'].mean(), yv['sales'].mean()

(10838.566258795981, 15746.483973127892)

## Error Analysis

In [118]:
yt = yt.merge(windows[['id_date', 'date']], on='id_date' )
yv = yv.merge(windows[['id_date', 'date']], on='id_date' )

In [119]:
yt['y_hat'] = yt_hat
yv['y_hat'] = yv_hat

In [180]:
yt['AE'] = np.abs(yt['sales']-yt['y_hat'])
yv['AE'] = np.abs(yv['sales']-yv['y_hat'])

Primero, podemos analizar en cuáles tiendas se tiene el mayor MAE y si este tiene relación con el comportamiento de la variable objetivo:

In [200]:
yt.groupby('store_nbr').agg({'AE':'mean'}).sort_values(by='AE',
                ascending=False).reset_index().reset_index().merge(yt.groupby('store_nbr').agg(
    {'sales':'mean'}).sort_values(by='sales',
                ascending=False).reset_index().reset_index(), on='store_nbr')[:15].T

0         1         2         3         4         5   \
index_x       0.000     1.000     2.000     3.000     4.000     5.000   
store_nbr    44.000    45.000    47.000    46.000     3.000    48.000   
AE         3198.133  2661.319  2532.869  2241.236  2127.996  2080.541   
index_y       0.000     1.000     2.000     4.000     3.000     6.000   
sales     34357.400 29813.423 27836.473 23148.635 27799.718 20057.111   

                 6         7         8         9         10        11  \
index_x       6.000     7.000     8.000     9.000    10.000    11.000   
store_nbr    49.000    51.000     9.000    11.000    50.000     7.000   
AE         1897.366  1644.916  1634.570  1600.146  1414.622  1383.536   
index_y       5.000     7.000    11.000     9.000    10.000    12.000   
sales     22891.187 18517.590 14772.302 15942.028 15845.137 14737.131   

                12        13        14  
index_x     12.000    13.000    14.000  
store_nbr   28.000     8.000    24.000  
AE        1335.924  1327.375  1304.615  
index_y     21.000     8.000    14.000  
sales     9960.025 16809.185 13121.731

In [201]:
yv.groupby('store_nbr').agg({'AE':'mean'}).sort_values(by='AE',
                ascending=False).reset_index().reset_index().merge(yv.groupby('store_nbr').agg(
    {'sales':'mean'}).sort_values(by='sales',
                ascending=False).reset_index().reset_index(), on='store_nbr')[:15].T

0         1         2         3         4         5   \
index_x       0.000     1.000     2.000     3.000     4.000     5.000   
store_nbr    45.000    44.000    47.000    46.000    51.000    49.000   
AE         6268.194  6126.605  5336.529  5233.804  5171.300  4744.834   
index_y       1.000     0.000     2.000     5.000     7.000     4.000   
sales     42760.349 47166.016 40103.725 31971.710 23762.970 37511.535   

                 6         7         8         9         10        11  \
index_x       6.000     7.000     8.000     9.000    10.000    11.000   
store_nbr     3.000    48.000    50.000    39.000     9.000    24.000   
AE         4588.367  4355.178  2978.075  2845.566  2767.458  2700.132   
index_y       3.000     6.000     9.000    15.000    12.000    14.000   
sales     38852.885 26614.628 21801.552 16507.319 19388.994 18156.472   

                 12        13        14  
index_x      12.000    13.000    14.000  
store_nbr     8.000    41.000    38.000  
AE         2663.482  2644.505  2631.209  
index_y       8.000    28.000    27.000  
sales     23417.564 12905.144 13236.463

En las tablas anteriores, podemos apreciar que existe una correlación significativa entre el promedio de la variable objetivo y y el MAE, es decir, el modelo se desempeña mejor en ventas pequeñas y peor en las ventas de cantidades grandes.

In [239]:
yt['APE'] = np.where(yt['AE']==0, 0, np.abs(yt['AE'] / (yt['sales']+1)))
yv['APE'] = np.where(yv['AE']==0, 0, np.abs(yv['AE'] / (yv['sales']+1)))

Dado lo anterior, podemos analizar si el Absolute Percentage Error, el error en porcentaje relativo al valor que se trata de predecir tiene el mismo comportamiento.

In [240]:
display(yt['APE'].replace([np.inf], np.nan).describe(percentiles=[.8,.95]).to_frame().T)
display(yv['APE'].replace([np.inf], np.nan).describe(percentiles=[.8,.95]).to_frame().T)

count  mean     std   min   50%   80%   95%       max
APE 72522.000 7.374 248.811 0.000 0.069 0.161 0.301 27628.516

count   mean     std   min   50%   80%   95%       max
APE 17928.000 24.222 567.069 0.000 0.107 0.226 0.413 24788.854

In [232]:
yt[(yt['sales']<100) & (yt['sales']==0)]

ancla  store_nbr   id_date  sales       date  y_hat    AE  APE
3        3.000     53.000  20130104  0.000 2013-01-04  0.000 0.000  NaN
18       3.000     29.000  20130104  0.000 2013-01-04  0.000 0.000  NaN
19       3.000     36.000  20130104  0.000 2013-01-04  0.000 0.000  NaN
22       3.000     42.000  20130104  0.000 2013-01-04  0.000 0.000  NaN
24       3.000     20.000  20130104  0.000 2013-01-04  0.000 0.000  NaN
...        ...        ...       ...    ...        ...    ...   ...  ...
72443 1344.000     18.000  20160909  0.000 2016-09-09  0.000 0.000  NaN
72462 1344.000     52.000  20160909  0.000 2016-09-09  0.000 0.000  NaN
72482 1345.000     25.000  20160910  0.000 2016-09-10  0.000 0.000  NaN
72497 1345.000     18.000  20160910  0.000 2016-09-10  0.000 0.000  NaN
72516 1345.000     52.000  20160910  0.000 2016-09-10  0.000 0.000  NaN

[6856 rows x 8 columns]

In [250]:
test_x = np.linspace(start=1e-2, stop=1-1e-3,num=30)
test_y = np.array(list(map(lambda x : np.log(x/(1-x)),np.linspace(start=1e-2, stop=1-1e-3,num=30))))

In [254]:
test_x

array([0.01      , 0.04410345, 0.0782069 , 0.11231034, 0.14641379,
       0.18051724, 0.21462069, 0.24872414, 0.28282759, 0.31693103,
       0.35103448, 0.38513793, 0.41924138, 0.45334483, 0.48744828,
       0.52155172, 0.55565517, 0.58975862, 0.62386207, 0.65796552,
       0.69206897, 0.72617241, 0.76027586, 0.79437931, 0.82848276,
       0.86258621, 0.89668966, 0.9307931 , 0.96489655, 0.999     ])

In [255]:
px.scatter(x=test_x, y=test_y)

In [258]:
70_000 * (1.10**(3/12))

71687.95823591115